In [23]:
from __future__ import (absolute_import, division, print_function,
                        unicode_literals)

import datetime  # For datetime objects
import os.path  # To manage paths
import sys  # To find out the script name (in argv[0])

import backtrader as bt
import backtrader.analyzers as btanalyzers
import pandas as pd
import numpy as np
import pickle

In [24]:
def moving_average(x, w):
        moving_avg = np.convolve(x, np.ones(w), 'valid') / w
        padding = np.full_like(np.empty(w), np.nan)
        return np.insert(moving_avg, 0, padding)

def moving_avg_diff(short, long):
        return (short - long) / long


def get_X_y(df, binary_output=True):
    
    min_period = 24*31 + 1
    
    percent_change = (df["Close"] - df["Close"].shift(1)) / df["Close"].shift(1)
    print(percent_change[:5])

    y = percent_change.copy()
    
    print(len(y))
    
    ## TEMP
    if binary_output == True:
        y = np.zeros(percent_change.shape)
        y[np.where(percent_change > 0)] = 1
    else:
        y = y.to_numpy()
    
    print(type(y))

    moving_average_1_hours = moving_average(df["Close"], 1)
    moving_average_2_hours = moving_average(df["Close"], 2)
    moving_average_3_hours = moving_average(df["Close"], 3)
    moving_average_12_hours = moving_average(df["Close"], 12)
    moving_average_24_hours = moving_average(df["Close"], 24)
    moving_average_48_hours = moving_average(df["Close"], 48)
    moving_average_1_week = moving_average(df["Close"], 24*7)
    moving_average_1_month = moving_average(df["Close"], 24*31)
    
    print(len(moving_average_1_month))
    
    mv_1h_2h = moving_avg_diff(moving_average_1_hours, moving_average_2_hours)
    mv_1h_3h = moving_avg_diff(moving_average_1_hours, moving_average_3_hours)
    mv_3h_12h = moving_avg_diff(moving_average_3_hours, moving_average_12_hours)
    mv_12h_24h = moving_avg_diff(moving_average_12_hours, moving_average_24_hours)
    mv_24h_48h = moving_avg_diff(moving_average_24_hours, moving_average_48_hours)
    mv_48h_1w = moving_avg_diff(moving_average_48_hours, moving_average_1_week)
    mv_1w_1m = moving_avg_diff(moving_average_1_week, moving_average_1_month)
    
    print(len(mv_1w_1m))
    
    X = np.stack((mv_1h_2h, mv_1h_3h, mv_3h_12h, mv_12h_24h, mv_24h_48h, mv_48h_1w, mv_1w_1m), axis=1)
    X = X[min_period:len(X)-1]
    y = y[min_period:]
    
    print(len(X), len(y))
    
    return (X, y)

In [25]:
df = pd.read_csv("../../data/clean/bitcoin_prices.csv")

df["Time"] = pd.to_datetime(df['Time'],unit='s')
df.set_index(pd.DatetimeIndex(df['Time']), inplace=True, drop=True)
start_date = datetime.datetime(2015,7,1)
df = df[df["Time"] > start_date]

offset = 24*31 + 1 # TODO: Refactor to output ox get_features
X, y = get_X_y(df)
df = df[offset:]
for i in range(0, len(X[0,:])):
    df["X_" + str(i)] = X[:,i]
df.describe()
print(df.columns)

Time
2015-07-20 21:00:00         NaN
2015-07-20 22:00:00    0.000504
2015-07-20 23:00:00    0.006687
2015-07-21 00:00:00    0.003179
2015-07-21 01:00:00   -0.001887
Name: Close, dtype: float64
47698
<class 'numpy.ndarray'>
47699
47699
46953 46953
Index(['Unnamed: 0', 'Time', 'Low', 'High', 'Open', 'Close', 'Volume', 'X_0',
       'X_1', 'X_2', 'X_3', 'X_4', 'X_5', 'X_6'],
      dtype='object')


In [26]:
class CommInfoFractional(bt.CommissionInfo):
    def getsize(self, price, cash):
        '''Returns fractional size for cash operation @price'''
        return self.p.leverage * (cash / price)

In [27]:
if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = bt.Cerebro()

    data = bt.feeds.PandasData(dataname=df)
    
    # Add the Data Feed to Cerebro
    cerebro.adddata(data)

    # Set our desired cash start
    cerebro.broker.setcash(10000.0)

    # Print out the starting conditions
    print('Starting Portfolio Value: %.2f' % cerebro.broker.getvalue())

    # Run over everything
    cerebro.run()

    # Print out the final result
    print('Final Portfolio Value: %.2f' % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
Final Portfolio Value: 10000.00


In [29]:
# Create a Stratey
class NNStrategy(bt.Strategy):

    def log(self, txt, dt=None):
        ''' Logging function fot this strategy'''
        dt = dt or self.datas[0].datetime.date(0)
        print('%s, %s' % (dt.isoformat(), txt))

    def __init__(self):
        self.dataclose = self.datas[0].close
        self.X_0 = self.datas[0].X_0
        self.X_1 = self.datas[0].X_1
        self.X_2 = self.datas[0].X_2
        self.X_3 = self.datas[0].X_3
        self.X_4 = self.datas[0].X_4
        self.X_5 = self.datas[0].X_5
        self.X_6 = self.datas[0].X_6

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None
        
        filename = "../../wip-models/pickles/svm_binary_classifier"
        self.clf = pickle.load(open(filename, 'rb'))

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    'BUY EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f' %
                    (order.executed.price,
                     order.executed.value,
                     order.executed.comm))

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log('SELL EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f' %
                         (order.executed.price,
                          order.executed.value,
                          order.executed.comm))

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log('Order Canceled/Margin/Rejected')

        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log('OPERATION PROFIT, feeGROSS %.2f, NET %.2f' %
                 (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log('Close, %.2f' % self.dataclose[0])
        print("Cash available: " + str(self.broker.get_cash()))
        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return
    
        X = [[self.X_0[0], self.X_1[0], self.X_2[0], self.X_3[0], self.X_4[0], self.X_5[0], self.X_6[0]]]
        pred = self.clf.predict(X)[0]
        print(pred)
        if not self.position:
            if pred == 1:
                self.log('BUY CREATE, %.2f' % self.dataclose[0])
                
                # Cancel existing orders 
                self.broker.cancel(self.order)
                
                self.buy(exectype=bt.Order.Market, size=(self.broker.get_cash() * 0.999 / self.data.close[0]))

                
                # Keep track of the created order to avoid a 2nd order
#                 self.order = self.buy()
#                 print(str(self.broker.get_cash() * 0.999 / self.data.close[0]), self.broker.get_cash(), self.data.close[0])
#                 self.buy(exectype=bt.Order.Market, size=(self.broker.get_cash() * 0.999 / self.data.close[0]))
#                 self.order = self.buy(exectype=bt.Order.Limit, size=size)
        elif self.position and pred == 0:
            
            ## TODO: figure out why it never sells all it's position
            self.log('SELL CREATE, %.2f' % self.dataclose[0])
            size = self.broker.get_value() / self.dataclose[0]
            self.sell(size=self.position.size)


class PandasData(bt.feeds.PandasData):
    params = (
        ('X_0', 'X_0'),
        ('X_1', 'X_1'),
        ('X_2', 'X_2'),
        ('X_3', 'X_3'),
        ('X_4', 'X_4'),
        ('X_5', 'X_5'),
        ('X_6', 'X_6'),
    )
    lines = ('X_0','X_1', 'X_2', 'X_3', 'X_4', 'X_5', 'X_6')

if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = bt.Cerebro()

    # Add a strategy
    cerebro.addstrategy(NNStrategy)

    data = PandasData(dataname=df)
    cerebro.adddata(data)

    cerebro.broker.setcash(10000)

    cerebro.addsizer(bt.sizers.FixedSize, stake=1)

    cerebro.broker.addcommissioninfo(CommInfoFractional())
    
    ## Include commission to see algo's returns with Coinbase Fees
    cerebro.broker.setcommission(commission=0.00075, margin=None) 
    cerebro.broker.set_coc(True)
    
    cerebro.addanalyzer(btanalyzers.SharpeRatio, _name='mysharpe')
    cerebro.addanalyzer(btanalyzers.AnnualReturn, _name='annualreturn')
    cerebro.addanalyzer(btanalyzers.DrawDown, _name='drawdown')
    cerebro.addanalyzer(btanalyzers.Returns, _name='returns')
    cerebro.addanalyzer(btanalyzers.TradeAnalyzer, _name='tradeanalyzer')

    cerebro.addobserver(bt.observers.DrawDown)

    print('Starting Portfolio Value: %.2f' % cerebro.broker.getvalue())

    strats = cerebro.run()

    print('Final Portfolio Value: %.2f' % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
2015-08-20, Close, 236.60
Cash available: 10000.0
1.0
2015-08-20, BUY CREATE, 236.60
2015-08-20, BUY EXECUTED, Price: 236.60, Cost: 9990.00, Comm 7.49
2015-08-20, Close, 235.56
Cash available: 2.5074999999999994
1.0
2015-08-21, Close, 235.76
Cash available: 2.5074999999999994
1.0
2015-08-21, Close, 234.04
Cash available: 2.5074999999999994
0.0
2015-08-21, SELL CREATE, 234.04
2015-08-21, SELL EXECUTED, Price: 234.04, Cost: 9990.00, Comm 7.41
2015-08-21, OPERATION PROFIT, feeGROSS -108.09, NET -123.00
2015-08-21, Close, 233.85
Cash available: 9877.004775147929
1.0
2015-08-21, BUY CREATE, 233.85
2015-08-21, BUY EXECUTED, Price: 233.85, Cost: 9867.13, Comm 7.40
2015-08-21, Close, 236.07
Cash available: 2.47665894736814
1.0
2015-08-21, Close, 235.27
Cash available: 2.47665894736814
0.0
2015-08-21, SELL CREATE, 235.27
2015-08-21, SELL EXECUTED, Price: 235.27, Cost: 9867.13, Comm 7.45
2015-08-21, OPERATION PROFIT, feeGROSS 59.92, NET 45.07
2015-08-21, Close,

Cash available: 9688.236671331822
0.0
2015-09-02, Close, 228.15
Cash available: 9688.236671331822
0.0
2015-09-02, Close, 228.29
Cash available: 9688.236671331822
0.0
2015-09-02, Close, 228.14
Cash available: 9688.236671331822
0.0
2015-09-02, Close, 228.92
Cash available: 9688.236671331822
1.0
2015-09-02, BUY CREATE, 228.92
2015-09-02, BUY EXECUTED, Price: 228.92, Cost: 9678.55, Comm 7.26
2015-09-02, Close, 228.29
Cash available: 2.429325345337194
0.0
2015-09-02, SELL CREATE, 228.29
2015-09-02, SELL EXECUTED, Price: 228.29, Cost: 9678.55, Comm 7.24
2015-09-02, OPERATION PROFIT, feeGROSS -26.64, NET -41.13
2015-09-02, Close, 228.58
Cash available: 9647.102946182451
1.0
2015-09-02, BUY CREATE, 228.58
2015-09-02, BUY EXECUTED, Price: 228.58, Cost: 9637.46, Comm 7.23
2015-09-02, Close, 228.80
Cash available: 2.4190110637555113
0.0
2015-09-02, SELL CREATE, 228.80
2015-09-02, SELL EXECUTED, Price: 228.80, Cost: 9637.46, Comm 7.24
2015-09-02, OPERATION PROFIT, feeGROSS 9.28, NET -5.19
2015-09-

2015-09-12, Close, 240.40
Cash available: 2.4011729261777557
1.0
2015-09-12, Close, 240.17
Cash available: 2.4011729261777557
1.0
2015-09-12, Close, 240.42
Cash available: 2.4011729261777557
1.0
2015-09-12, Close, 240.47
Cash available: 2.4011729261777557
0.0
2015-09-12, SELL CREATE, 240.47
2015-09-12, SELL EXECUTED, Price: 240.47, Cost: 9566.39, Comm 7.16
2015-09-12, OPERATION PROFIT, feeGROSS -16.28, NET -30.62
2015-09-12, Close, 240.61
Cash available: 9545.34356828719
1.0
2015-09-12, BUY CREATE, 240.61
2015-09-12, BUY EXECUTED, Price: 240.61, Cost: 9535.80, Comm 7.15
2015-09-12, Close, 240.16
Cash available: 2.3934948997474486
0.0
2015-09-12, SELL CREATE, 240.16
2015-09-12, SELL EXECUTED, Price: 240.16, Cost: 9535.80, Comm 7.14
2015-09-12, OPERATION PROFIT, feeGROSS -17.83, NET -32.12
2015-09-12, Close, 239.68
Cash available: 9513.218953826037
1.0
2015-09-12, BUY CREATE, 239.68
2015-09-12, BUY EXECUTED, Price: 239.68, Cost: 9503.71, Comm 7.13
2015-09-12, Close, 239.56
Cash available

2015-09-18, OPERATION PROFIT, feeGROSS 36.29, NET 22.67
2015-09-18, Close, 233.40
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.41
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.40
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.75
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.95
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.79
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.76
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.47
Cash available: 9090.490276009976
0.0
2015-09-18, Close, 233.78
Cash available: 9090.490276009976
1.0
2015-09-18, BUY CREATE, 233.78
2015-09-19, BUY EXECUTED, Price: 233.78, Cost: 9081.40, Comm 6.81
2015-09-19, Close, 234.12
Cash available: 2.279440436709841
0.0
2015-09-19, SELL CREATE, 234.12
2015-09-19, SELL EXECUTED, Price: 234.12, Cost: 9081.40, Comm 6.82
2015-09-19, OPERATION PROFIT, feeGROSS 13.21, NET -0.42
2015-09-19, Close, 232.81
Cash available: 9090.06588

2015-09-28, Close, 239.86
Cash available: 2.2164676128992493
1.0
2015-09-28, Close, 239.33
Cash available: 2.2164676128992493
0.0
2015-09-28, SELL CREATE, 239.33
2015-09-28, SELL EXECUTED, Price: 239.33, Cost: 8830.51, Comm 6.65
2015-09-28, OPERATION PROFIT, feeGROSS 40.40, NET 27.13
2015-09-28, Close, 239.99
Cash available: 8866.477848287259
1.0
2015-09-28, BUY CREATE, 239.99
2015-09-29, BUY EXECUTED, Price: 239.99, Cost: 8857.61, Comm 6.64
2015-09-29, Close, 238.80
Cash available: 2.2232693204578746
0.0
2015-09-29, SELL CREATE, 238.80
2015-09-29, SELL EXECUTED, Price: 238.80, Cost: 8857.61, Comm 6.61
2015-09-29, OPERATION PROFIT, feeGROSS -43.92, NET -57.17
2015-09-29, Close, 239.00
Cash available: 8809.303552100495
1.0
2015-09-29, BUY CREATE, 239.00
2015-09-29, BUY EXECUTED, Price: 239.00, Cost: 8800.49, Comm 6.60
2015-09-29, Close, 239.66
Cash available: 2.208932865688367
1.0
2015-09-29, Close, 239.65
Cash available: 2.208932865688367
0.0
2015-09-29, SELL CREATE, 239.65
2015-09-29,

...

Cash available: 0.03006196184413977
1.0
2020-11-23, Close, 18384.82
Cash available: 0.03006196184413977
1.0
2020-11-24, Close, 18375.70
Cash available: 0.03006196184413977
1.0
2020-11-24, Close, 18485.11
Cash available: 0.03006196184413977
1.0
2020-11-24, Close, 18360.00
Cash available: 0.03006196184413977
0.0
2020-11-24, SELL CREATE, 18360.00
2020-11-24, SELL EXECUTED, Price: 18360.00, Cost: 119.77, Comm 0.09
2020-11-24, OPERATION PROFIT, feeGROSS -1.79, NET -1.96
2020-11-24, Close, 18367.39
Cash available: 117.92368767355721
1.0
2020-11-24, BUY CREATE, 18367.39
2020-11-24, BUY EXECUTED, Price: 18367.39, Cost: 117.81, Comm 0.09
2020-11-24, Close, 18462.67
Cash available: 0.029569364684140245
1.0
2020-11-24, Close, 18350.13
Cash available: 0.029569364684140245
0.0
2020-11-24, SELL CREATE, 18350.13
2020-11-24, SELL EXECUTED, Price: 18350.13, Cost: 117.81, Comm 0.09
2020-11-24, OPERATION PROFIT, feeGROSS -0.11, NET -0.29
2020-11-24, Close, 18413.67
Cash available: 117.63635892908962
1.0


2020-12-03, SELL EXECUTED, Price: 19390.91, Cost: 113.11, Comm 0.09
2020-12-03, OPERATION PROFIT, feeGROSS 2.14, NET 1.97
2020-12-03, Close, 19375.00
Cash available: 115.18852077870388
0.0
2020-12-03, Close, 19364.44
Cash available: 115.18852077870388
0.0
2020-12-03, Close, 19411.84
Cash available: 115.18852077870388
1.0
2020-12-03, BUY CREATE, 19411.84
2020-12-03, BUY EXECUTED, Price: 19411.84, Cost: 115.07, Comm 0.09
2020-12-03, Close, 19350.11
Cash available: 0.028883521585257907
0.0
2020-12-03, SELL CREATE, 19350.11
2020-12-03, SELL EXECUTED, Price: 19350.11, Cost: 115.07, Comm 0.09
2020-12-03, OPERATION PROFIT, feeGROSS -0.37, NET -0.54
2020-12-03, Close, 19302.30
Cash available: 114.65024996749959
1.0
2020-12-03, BUY CREATE, 19302.30
2020-12-03, BUY EXECUTED, Price: 19302.30, Cost: 114.54, Comm 0.09
2020-12-03, Close, 19370.06
Cash available: 0.028748550179347535
1.0
2020-12-03, Close, 19556.13
Cash available: 0.028748550179347535
1.0
2020-12-03, Close, 19380.28
Cash available: 0

2020-12-11, Close, 17800.00
Cash available: 0.026634280255808426
1.0
2020-12-11, Close, 17886.29
Cash available: 0.026634280255808426
1.0
2020-12-11, Close, 17799.00
Cash available: 0.026634280255808426
0.0
2020-12-11, SELL CREATE, 17799.00
2020-12-11, SELL EXECUTED, Price: 17799.00, Cost: 106.11, Comm 0.08
2020-12-11, OPERATION PROFIT, feeGROSS -0.56, NET -0.72
2020-12-11, Close, 17741.90
Cash available: 105.49772104949155
1.0
2020-12-11, BUY CREATE, 17741.90
2020-12-11, BUY EXECUTED, Price: 17741.90, Cost: 105.39, Comm 0.08
2020-12-11, Close, 17639.93
Cash available: 0.026453553553156747
1.0
2020-12-11, Close, 17860.00
Cash available: 0.026453553553156747
1.0
2020-12-11, Close, 17970.13
Cash available: 0.026453553553156747
0.0
2020-12-11, SELL CREATE, 17970.13
2020-12-11, SELL EXECUTED, Price: 17970.13, Cost: 105.39, Comm 0.08
2020-12-11, OPERATION PROFIT, feeGROSS 1.36, NET 1.20
2020-12-11, Close, 18059.60
Cash available: 106.69437075720585
0.0
2020-12-11, Close, 18107.72
Cash avail

2020-12-21, Close, 23958.28
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23909.78
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23913.91
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23935.75
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23974.83
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23656.28
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23460.28
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 22425.51
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 22646.11
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 22308.45
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 22837.00
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23191.13
Cash available: 0.031031099444718907
1.0
2020-12-21, Close, 23126.53
Cash available: 0.031031099444718907
0.0
2020-12-21, SELL CREATE, 23126.53
2020-12-21, SELL EXECUTED, Price: 23126.53, Cost: 123.63, Comm 0.09
2

Final Portfolio Value: 133.94


In [ ]:
print('Returns:', strats[0].analyzers.returns.pprint())
print('Sharpe Ratio:', strats[0].analyzers.mysharpe.pprint())
print('Annual Return:', strats[0].analyzers.annualreturn.pprint())
print('Drawdown:', strats[0].analyzers.drawdown.pprint())
print('Trade Analyzer:', strats[0].analyzers.tradeanalyzer.pprint())

In [11]:
cerebro.plot()

ImportError: cannot import name 'warnings' from 'matplotlib.dates' (/usr/local/lib/python3.9/site-packages/matplotlib/dates.py)